In [2]:
import json
import pandas as pd
import nltk
nltk.data.path = ['/home/albin/nltk_data']
nltk.download('punkt_tab')
nltk.download('averaged_perceptron_tagger_eng')


from pathlib import Path
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.data import find
find("tokenizers/punkt")


[nltk_data] Downloading package punkt_tab to /home/albin/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger_eng to
[nltk_data]     /home/albin/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger_eng is already up-to-
[nltk_data]       date!


FileSystemPathPointer('/home/albin/nltk_data/tokenizers/punkt')

In [20]:
class Summary:
    def read_jsonl_to_df(self) -> pd.DataFrame:
        with open("../output/data.jsonl") as f:
            f = f.readlines()
            f = [json.loads(line) for line in f]
            r = []
            for i in f:
                r.append(pd.DataFrame(i, index=[0]))
            
            df = pd.concat(r, ignore_index=True)
            data   = df.copy().drop_duplicates()
            return data
    
    def average_stats(self, data: pd.DataFrame) -> None:
        data['words'] = data['content'].apply(lambda x: len(x.split()))
        data['chars'] = data['content'].apply(lambda x: len(x))
        data['sentences'] = data['content'].apply(lambda x: len(x.split('.')))
        data['paragraphs'] = data['content'].apply(lambda x: len(x.split('\n')))
        data['avg_word_length'] = data['chars'] / data['words']
        result = data.groupby('media_type').agg({'sentences': 'mean', 'words': 'mean', 'chars': 'mean', 'paragraphs': 'mean', 'avg_word_length': 'mean'}).reset_index().round(0)
        
        print(
        "N sample: %s \n\n"
        "Average lenght of words, sentences, paragraphs:" \
        "\n\n %s" %(len(data), result), end="\n\n"
        )

    def nltk_stats(self, title, sentence) -> None:
        print("nltk.data.paths: ", nltk.data.path)

        stop_words = nltk.corpus.stopwords.words('english')
        tokens: list = nltk.word_tokenize(sentence)
        filtered_sentence = [w for w in tokens if not w.lower() in stop_words]
        tagged: list[tuple] = nltk.pos_tag(filtered_sentence)
        nouns = [word for word, pos in tagged if pos in ['NNP']]
        for noun in nouns:
            print(
            "Title: %s \n",
            {"Entity": noun,
            "Sentence": sentence,
            }
            )
    
    def run(self):
        data: pd.DataFrame = self.read_jsonl_to_df()
        self.average_stats(data)
        for i in data.iterrows():
            self.nltk_stats(i[1]['title'], i[1]['content'])
        

Summary().run()

N sample: 907 

Average lenght of words, sentences, paragraphs:

   media_type  sentences   words   chars  paragraphs  avg_word_length
0    article       31.0   729.0  4401.0        25.0              6.0
1       blog       57.0  1062.0  6528.0        22.0              6.0
2   liveblog        2.0    31.0   188.0         1.0              6.0

nltk.data.paths:  ['/home/albin/nltk_data']
Title: %s 
 {'Entity': 'Edan', 'Sentence': 'Following the release of Edan Alexander from Gaza, the head of the Health Ministry’s medical division, Dr. Hagar Mizrahi, says she is “very concerned” about the health and well-being of the remaining hostages.'}
Title: %s 
 {'Entity': 'Alexander', 'Sentence': 'Following the release of Edan Alexander from Gaza, the head of the Health Ministry’s medical division, Dr. Hagar Mizrahi, says she is “very concerned” about the health and well-being of the remaining hostages.'}
Title: %s 
 {'Entity': 'Gaza', 'Sentence': 'Following the release of Edan Alexander from Gaza, t

KeyboardInterrupt: 